In [0]:
# verifica se o arquivo existe na volume
file_path = 'dbfs:/Volumes/bcb/pix/pix/Transações Pix por Município.csv'

try:
    files = dbutils.fs.ls('dbfs:/Volumes/bcb/pix/pix/')
    if any(f.name == 'Transações Pix por Município.csv' for f in files):
        print("Arquivo existe !")
    else:
        print("Arquivo não encontrado !")
except Exception as e:
    print("Erro:", e)

Erro: (com.databricks.sql.managedcatalog.acl.UnauthorizedAccessException) PERMISSION_DENIED: User does not have USE CATALOG on Catalog 'bcb'.

JVM stacktrace:
com.databricks.sql.managedcatalog.acl.UnauthorizedAccessException
	at com.databricks.managedcatalog.ErrorDetailsHandler.wrapServiceException(ErrorDetailsHandler.scala:98)
	at com.databricks.managedcatalog.ErrorDetailsHandler.wrapServiceException$(ErrorDetailsHandler.scala:69)
	at com.databricks.managedcatalog.ManagedCatalogClientImpl.wrapServiceException(ManagedCatalogClientImpl.scala:40)
	at com.databricks.sql.managedcatalog.client.ManagedCatalogClientImpl.recordAndWrapExceptionBase(ManagedCatalogClientImpl.scala:7878)
	at com.databricks.sql.managedcatalog.client.ManagedCatalogClientImpl.recordAndWrapException(ManagedCatalogClientImpl.scala:7862)
	at com.databricks.sql.managedcatalog.client.ManagedCatalogClientImpl.generateTemporaryVolumeCredentials(ManagedCatalogClientImpl.scala:9055)
	at com.databricks.sql.managedcatalog.Manag

In [0]:
from pyspark.sql.functions import col, regexp_replace, concat_ws, lit, to_date
from pyspark.sql.types import DecimalType

# Lê o CSV
df = (
    spark.read.format("csv")
    .option("header", "true")
    .option("inferSchema", "true")
    .load(file_path)
)

# --- Tratamento da coluna AnoMes ---
df = (
    df.withColumn("AnoMes", col("AnoMes").cast("string"))  # garante string
      .withColumn("AnoMes", regexp_replace(col("AnoMes"), r"(\d{4})(\d{2})", "$1-$2"))  # 202401 -> 2024-01
      .withColumn("AnoMes", to_date(concat_ws("-", col("AnoMes"), lit("01")), "yyyy-MM-dd"))  # adiciona dia 01
)

# --- Conversão de valores monetários ---
colunas_valor = ["VL_PagadorPF", "VL_PagadorPJ", "VL_RecebedorPF", "VL_RecebedorPJ"]

for c in colunas_valor:
    # Substitui vírgula decimal por ponto
    df = df.withColumn(c, regexp_replace(col(c).cast("string"), ",", "."))
    # Converte para decimal (18,2) — seguro para valores grandes
    df = df.withColumn(c, col(c).cast(DecimalType(18, 2)))

# Exibe o resultado
display(df)


---------------------------------------------------------------------------
UnknownException                          Traceback (most recent call last)
File <command-7210178048576092>, line 29
     26     df = df.withColumn(c, col(c).cast(DecimalType(18, 2)))
     28 # Exibe o resultado
---> 29 display(df)

File /databricks/python_shell/lib/dbruntime/display.py:133, in Display.display(self, input, *args, **kwargs)
    131     pass
    132 elif self._cf_helper is not None and isinstance(input, ConnectDataFrame):
--> 133     self.display_connect_table(input, **kwargs)
    134 elif isinstance(input, ConnectDataFrame):
    135     if input.isStreaming:

File /databricks/python_shell/lib/dbruntime/display.py:93, in Display.display_connect_table(self, df, **kwargs)
     88 except Exception as e:
     89     raise type(
     90         e
     91     )("IPython shell encountered an error or was missing data, please restart the notebook or contact Databricks support"
     92       ) from e
--->

In [0]:
# valor total pago por pessoas fisicas por mes ano e municipio

import pyspark.sql.functions as F

df_per_year_pf_pago = (
    df.groupBy(
        F.year(df.AnoMes).alias("Ano"),
        df.Municipio_Ibge,
        df.Municipio
    ).agg(
        F.sum(df.VL_PagadorPF).alias("Valor_total_pago_PF")
    )
)

display(df_per_year_pf_pago)

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-7210178048576093>, line 6
      1 # valor total pago por pessoas fisicas por mes ano e municipio
      3 import pyspark.sql.functions as F
      5 df_per_year_pf_pago = (
----> 6     df.groupBy(
      7         F.year(df.AnoMes).alias("Ano"),
      8         df.Municipio_Ibge,
      9         df.Municipio
     10     ).agg(
     11         F.sum(df.VL_PagadorPF).alias("Valor_total_pago_PF")
     12     )
     13 )
     15 display(df_per_year_pf_pago)

NameError: name 'df' is not defined

In [0]:
# valor total pago por pessoas juridicas por mes ano e municipio

import pyspark.sql.functions as F

df_per_year_pj_pago = (
    df.groupBy(
        F.year(df.AnoMes).alias("Ano"),
        df.Municipio_Ibge,
        df.Municipio
    ).agg(
        F.sum(df.VL_PagadorPJ).alias("Valor_total_pago_PJ")
    )
)

display(df_per_year_pj_pago)


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-5448391543758046>, line 6
      1 # valor total pago por pessoas juridicas por mes ano e municipio
      3 import pyspark.sql.functions as F
      5 df_per_year_pj_pago = (
----> 6     df.groupBy(
      7         F.year(df.AnoMes).alias("Ano"),
      8         df.Municipio_Ibge,
      9         df.Municipio
     10     ).agg(
     11         F.sum(df.VL_PagadorPJ).alias("ValorTotalPagoPJ")
     12     )
     13 )
     15 display(df_per_year_pj_pago)

NameError: name 'df' is not defined

In [0]:
import pyspark.sql.functions as F

# total por estado
df_per_year_estado = (
    df.groupBy(
        df.Estado,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_PagadorPF+df.VL_PagadorPJ).alias("Total Pago Estado")
    )
)

display(df_per_year_estado)

Estado Ano Total Pago Estado CEARÁ 2023 389662338443.93 TOCANTINS 2025 128177715238.29 RONDÔNIA 2023 97868184755.80 MINAS GERAIS 2022 867200267479.34 MINAS GERAIS 2025 1689691342897.95 ALAGOAS 2021 30897648350.93 RIO GRANDE DO SUL 2024 1076257212841.65 MINAS GERAIS 2021 431800975453.50 RORAIMA 2020 264330819.74 PARANÁ 2022 701993428389.08 RONDÔNIA 2021 33859628155.56 TOCANTINS 2020 815442358.44 RORAIMA 2024 49057069209.39 ESPÍRITO SANTO 2025 390192423407.17 GOIÁS 2020 5620026168.63 RIO GRANDE DO SUL 2022 493338199847.93 PARANÁ 2025 1484712191059.03 AMAPÁ 2022 22993132159.04 CEARÁ 2020 3453467552.13 TOCANTINS 2024 142837536781.64 RIO DE JANEIRO 2021 380463311730.00 SERGIPE 2025 124397608693.91 RIO GRANDE DO NORTE 2021 49220612679.15 SERGIPE 2024 141636860624.46 RONDÔNIA 2022 69475916114.83 RIO DE JANEIRO 2020 10637252666.83 ESPÍRITO SANTO 2020 2506335529.21 GOIÁS 2021 196702947215.10 RORAIMA 2023 33064684006.40 PIAUÍ 2023 108873491132.02 MATO GROSSO DO SUL 2020 1693499745.10 AMAZONAS 2023 207168568655.14 RORAIMA 2022 24565743553.64 BAHIA 2024 939705672093.63 PARAÍBA 2021 44450566092.02 SANTA CATARINA 2022 435110637263.28 SERGIPE 2021 26843931849.20 PIAUÍ 2025 162200883699.68 SANTA CATARINA 2020 7049847294.99 MATO GROSSO DO SUL 2021 66353752660.66 ACRE 2024 50660049631.27 MARANHÃO 2024 436948574056.18 ACRE 2021 9760214539.33 SÃO PAULO 2025 7047101604202.96 MATO GROSSO DO SUL 2023 205836997695.81 MATO GROSSO DO SUL 2024 294084985576.98 BAHIA 2021 188030937148.44 PARANÁ 2020 10672267856.93 MARANHÃO 2022 168887153306.80 AMAZONAS 2020 1904478519.22 BAHIA 2025 794005593961.32 BAHIA 2020 5723516293.28 RIO GRANDE DO SUL 2020 5989108608.98 ALAGOAS 2022 73378452569.93 ESPÍRITO SANTO 2023 256493179940.38 SANTA CATARINA 2025 904953828477.15 MATO GROSSO 2020 3125410420.40 PARAÍBA 2025 209040363458.60 PERNAMBUCO 2025 519835510738.65 ACRE 2025 44534919084.57 PARAÍBA 2022 95960093572.40 RIO DE JANEIRO 2025 1726610440951.87 PARÁ 2022 232365991627.41 PARANÁ 2023 1099523284931.04 PIAUÍ 2022 70213293025.43 SÃO PAULO 2020 41329938803.57 RIO GRANDE DO NORTE 2022 98563979407.64 AMAPÁ 2025 44406299448.63 RONDÔNIA 2020 958992349.18 ALAGOAS 2024 176941834920.72 AMAZONAS 2024 322753372109.09 RIO GRANDE DO NORTE 2024 207696403124.89 RIO GRANDE DO SUL 2025 961436970983.76 PARANÁ 2024 1619261793152.71 ESPÍRITO SANTO 2022 171129842070.96 PIAUÍ 2021 31035722966.68 SANTA CATARINA 2023 651401769899.37 PARAÍBA 2020 1325939582.65 RONDÔNIA 2024 142491760994.67 PARÁ 2020 2737116612.26 PARÁ 2025 446288490700.86 SÃO PAULO 2023 4694874748881.99 PERNAMBUCO 2022 271039276091.08 BAHIA 2022 407065300763.51 SÃO PAULO 2024 7429607333867.14 TOCANTINS 2022 63351057762.70 GOIÁS 2023 557702833054.23 PARÁ 2024 505360862818.71 AMAPÁ 2020 303037488.89 MARANHÃO 2023 261961768688.45 MATO GROSSO 2022 235085733591.68 RIO GRANDE DO SUL 2023 750749728323.74 MINAS GERAIS 2020 12735558646.56 SANTA CATARINA 2024 1010637852261.70 PARÁ 2023 339050010475.87 SERGIPE 2023 94983471090.62 RORAIMA 2025 43696858258.16 ESPÍRITO SANTO 2021 80642735520.19 MINAS GERAIS 2024 1867543757796.54 SERGIPE 2020 736661838.79 RORAIMA 2021 10301892471.80 PARANÁ 2021 352650532503.28 MATO GROSSO 2025 488801641473.22 GOIÁS 2022 395422959311.85 CEARÁ 2021 118654961962.77 PARAÍBA 2023 147941392427.94 SANTA CATARINA 2021 225721433213.11 CEARÁ 2024 576906499312.87 MARANHÃO 2021 71741732608.23 MATO GROSSO 2023 354576411070.60 ACRE 2022 21339873383.97 PIAUÍ 2024 162499790986.48 RONDÔNIA 2025 127312835441.53 SÃO PAULO 2022 2924125831720.28 AMAZONAS 2025 262745433692.83 PERNAMBUCO 2020 3580556729.03 MATO GROSSO 2021 105041768294.37 MINAS GERAIS 2023 1256985048294.69 PERNAMBUCO 2023 395907466221.33 ACRE 2020 271640321.16 RIO GRANDE DO SUL 2021 236600569367.09 CEARÁ 2022 257183061693.86 ESPÍRITO SANTO 2024 406660799215.64 ALAGOAS 2020 801240941.30 ALAGOAS 2023 120034343321.72 AMAPÁ 2024 50899099314.68 MARANHÃO 2025 367320886464.29 ACRE 2023 32782964668.83 AMAPÁ 2021 10589605865.29 RIO DE JANEIRO 2022 845053792267.80 GOIÁS 202

In [0]:
import pyspark.sql.functions as F

# total por regiao
df_per_year_regiao = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_PagadorPF+df.VL_PagadorPJ).alias("Total Pago Região")
    )
)

display(df_per_year_regiao)

Regiao Ano Total Pago Região SUDESTE 2024 11629489088377.25 SUL 2021 814972535083.48 NORTE 2023 841996703186.53 SUDESTE 2022 4807509733538.38 NORTE 2021 256631697002.29 SUL 2023 2501674783154.15 SUDESTE 2025 10853595811459.95 CENTRO-OESTE 2022 952256777143.72 SUL 2025 3351102990519.94 SUDESTE 2021 2284658946740.44 NORTE 2020 7255038468.89 SUDESTE 2023 7428315559799.91 NORDESTE 2023 2279235239961.43 SUDESTE 2020 67209085646.17 SUL 2020 23711223760.90 NORTE 2025 1097162551864.87 CENTRO-OESTE 2020 14287084014.21 NORDESTE 2021 688229727941.67 CENTRO-OESTE 2023 1387029894141.26 NORDESTE 2024 3459513830559.73 NORDESTE 2022 1504254415128.01 NORTE 2024 1264059750859.45 CENTRO-OESTE 2021 474452158113.37 NORDESTE 2020 19759817512.47 SUL 2024 3706156858256.06 CENTRO-OESTE 2024 2047635531414.19 NORDESTE 2025 3030976064954.14 CENTRO-OESTE 2025 1871009528606.40 NORTE 2022 573697418905.91 SUL 2022 1630442265500.29 Nao informado 2022 6632713627.87 Nao informado 2023 8448368337.19 Nao informado 2021 3122788970.11 Nao informado 2020 64718567.45 Nao informado 2025 23386029688.12 Nao informado 2024 13837889923.51

In [0]:
import pyspark.sql.functions as F

# total recebido por regiao
df_per_year_regiao_recebedor = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_RecebedorPF+df.VL_RecebedorPJ).alias("Total Recebido Região")
    )
)

display(df_per_year_regiao_recebedor)

Regiao Ano Total Recebido Região SUDESTE 2024 11567890425054.20 SUL 2021 822476592748.43 NORTE 2023 835010957647.00 SUDESTE 2022 4781076175758.35 NORTE 2021 254498170842.49 SUL 2023 2530658234806.34 SUDESTE 2025 10825016315327.69 CENTRO-OESTE 2022 955565924259.94 SUL 2025 3297761280186.90 SUDESTE 2021 2287179506988.90 NORTE 2020 7115723551.38 SUDESTE 2023 7398969064819.00 NORDESTE 2023 2272451680344.73 SUDESTE 2020 67757030254.13 SUL 2020 23741562950.18 NORTE 2025 1079212412272.95 CENTRO-OESTE 2020 13933896140.05 NORDESTE 2021 685303701476.07 CENTRO-OESTE 2023 1400595826610.25 NORDESTE 2024 3406644060290.35 NORDESTE 2022 1501421397063.34 NORTE 2024 1242220710005.81 CENTRO-OESTE 2021 470569709339.32 NORDESTE 2020 19670043314.01 SUL 2024 3710443284659.49 CENTRO-OESTE 2024 2176180058194.06 NORDESTE 2025 2966402167195.50 CENTRO-OESTE 2025 2027981299861.45 NORTE 2022 569195439101.40 SUL 2022 1662638132273.99 Nao informado 2022 4896255387.16 Nao informado 2023 9014784353.15 Nao informado 2021 2032656311.92 Nao informado 2020 68711760.34 Nao informado 2025 30859502248.93 Nao informado 2024 17314411186.28

In [0]:
import pyspark.sql.functions as F

# total recebido por regiao
df_per_year_estado_recebedor = (
    df.groupBy(
        df.Estado,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_RecebedorPF+df.VL_RecebedorPJ).alias("Total Recebido Estado")
    )
)

display(df_per_year_estado_recebedor)

Estado Ano Total Recebido Estado CEARÁ 2023 384146463366.49 TOCANTINS 2025 124121637620.89 RONDÔNIA 2023 98086805014.16 MINAS GERAIS 2022 852124125899.69 MINAS GERAIS 2025 1656308143248.92 ALAGOAS 2021 30838262688.23 RIO GRANDE DO SUL 2024 1084503927377.48 MINAS GERAIS 2021 418597916869.08 RORAIMA 2020 242100526.31 PARANÁ 2022 716028499415.26 RONDÔNIA 2021 32994749683.70 TOCANTINS 2020 800090736.62 RORAIMA 2024 48351903094.88 ESPÍRITO SANTO 2025 384950792618.95 GOIÁS 2020 5362616300.09 RIO GRANDE DO SUL 2022 495377186982.91 PARANÁ 2025 1458397687216.62 AMAPÁ 2022 22589496824.47 CEARÁ 2020 3471905937.26 TOCANTINS 2024 137987064237.07 RIO DE JANEIRO 2021 369073730421.82 SERGIPE 2025 121590349071.52 RIO GRANDE DO NORTE 2021 48880622089.91 SERGIPE 2024 140968222463.81 RONDÔNIA 2022 68202869580.52 RIO DE JANEIRO 2020 10604766183.53 ESPÍRITO SANTO 2020 2491223037.49 GOIÁS 2021 193709697189.22 RORAIMA 2023 32964759272.87 PIAUÍ 2023 106198929811.22 MATO GROSSO DO SUL 2020 1682315211.68 AMAZONAS 2023 206589886936.57 RORAIMA 2022 24888704101.82 BAHIA 2024 951951631748.32 PARAÍBA 2021 46269366415.50 SANTA CATARINA 2022 451232445875.82 SERGIPE 2021 26859650380.87 PIAUÍ 2025 158539268071.74 SANTA CATARINA 2020 7118686660.52 MATO GROSSO DO SUL 2021 66218953623.57 ACRE 2024 48473570496.06 MARANHÃO 2024 410990335819.74 ACRE 2021 9520402528.33 SÃO PAULO 2025 7028702562173.67 MATO GROSSO DO SUL 2023 201295567947.29 MATO GROSSO DO SUL 2024 284542959979.89 BAHIA 2021 189627604775.12 PARANÁ 2020 10527878521.52 MARANHÃO 2022 158131221126.29 AMAZONAS 2020 1896416053.56 BAHIA 2025 787591439629.34 BAHIA 2020 5626168678.65 RIO GRANDE DO SUL 2020 6094997768.14 ALAGOAS 2022 72812545817.62 ESPÍRITO SANTO 2023 254704403441.22 SANTA CATARINA 2025 889541678998.44 MATO GROSSO 2020 3109912885.77 PARAÍBA 2025 205000390871.26 PERNAMBUCO 2025 514874720089.44 ACRE 2025 42433131631.66 PARAÍBA 2022 98720640932.69 RIO DE JANEIRO 2025 1755054817286.15 PARÁ 2022 231139169961.49 PARANÁ 2023 1108936589075.58 PIAUÍ 2022 69635109602.48 SÃO PAULO 2020 41929949240.08 RIO GRANDE DO NORTE 2022 99926006083.38 AMAPÁ 2025 43800026149.18 RONDÔNIA 2020 934934288.84 ALAGOAS 2024 171911515200.17 AMAZONAS 2024 320509222359.60 RIO GRANDE DO NORTE 2024 204521141094.83 RIO GRANDE DO SUL 2025 949821913971.84 PARANÁ 2024 1629667981525.98 ESPÍRITO SANTO 2022 170969397657.82 PIAUÍ 2021 30858755896.30 SANTA CATARINA 2023 659322561887.10 PARAÍBA 2020 1379186327.08 RONDÔNIA 2024 142201984601.55 PARÁ 2020 2687120465.72 PARÁ 2025 436618820042.05 SÃO PAULO 2023 4749413774821.61 PERNAMBUCO 2022 265945766746.38 BAHIA 2022 414593212910.27 SÃO PAULO 2024 7524451849121.15 TOCANTINS 2022 63638180634.24 GOIÁS 2023 562892074419.80 PARÁ 2024 495462797295.15 AMAPÁ 2020 293898632.97 MARANHÃO 2023 245616145853.47 MATO GROSSO 2022 235489348235.13 RIO GRANDE DO SUL 2023 762399083843.66 MINAS GERAIS 2020 12731091793.03 SANTA CATARINA 2024 996271375756.03 PARÁ 2023 336360965250.90 SERGIPE 2023 95954170917.34 RORAIMA 2025 42871077090.83 ESPÍRITO SANTO 2021 82240049104.97 MINAS GERAIS 2024 1825382984279.42 SERGIPE 2020 736895074.27 RORAIMA 2021 9939337846.77 PARANÁ 2021 356623085100.18 MATO GROSSO 2025 475589292915.31 GOIÁS 2022 393390651454.47 CEARÁ 2021 119792039246.49 PARAÍBA 2023 150047948276.79 SANTA CATARINA 2021 230185491799.02 CEARÁ 2024 560039305007.08 MARANHÃO 2021 67322251562.95 MATO GROSSO 2023 354039127804.25 ACRE 2022 20777033603.79 PIAUÍ 2024 156213100885.32 RONDÔNIA 2025 126865877171.79 SÃO PAULO 2022 2947133450128.55 AMAZONAS 2025 262501842566.55 PERNAMBUCO 2020 3582428444.04 MATO GROSSO 2021 106620203649.89 MINAS GERAIS 2023 1239356589602.04 PERNAMBUCO 2023 394566561309.01 ACRE 2020 261162847.36 RIO GRANDE DO SUL 2021 235668015849.23 CEARÁ 2022 259798306115.07 ESPÍRITO SANTO 2024 401117387538.10 ALAGOAS 2020 808469454.20 ALAGOAS 2023 118347164318.25 AMAPÁ 2024 49234167921.50 MARANHÃO 2025 349605321219.62 ACRE 2023 31498276552.40 AMAPÁ 2021 10307921519.26 RIO DE JANEIRO 2022 810849202072.29 GOIÁS 2

In [0]:
import pyspark.sql.functions as F

# Total recebido e pago por Estado e Ano
df_estado_ano = (
    df.groupBy(
        df.Estado,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_RecebedorPF + df.VL_RecebedorPJ).alias("Total_Recebido"),
        F.sum(df.VL_PagadorPF + df.VL_PagadorPJ).alias("Total_Pago")
    )
    .orderBy("Estado", "Ano")
)

display(df_estado_ano)

Estado Ano Total_Recebido Total_Pago ACRE 2020 261162847.36 271640321.16 ACRE 2021 9520402528.33 9760214539.33 ACRE 2022 20777033603.79 21339873383.97 ACRE 2023 31498276552.40 32782964668.83 ACRE 2024 48473570496.06 50660049631.27 ACRE 2025 42433131631.66 44534919084.57 ALAGOAS 2020 808469454.20 801240941.30 ALAGOAS 2021 30838262688.23 30897648350.93 ALAGOAS 2022 72812545817.62 73378452569.93 ALAGOAS 2023 118347164318.25 120034343321.72 ALAGOAS 2024 171911515200.17 176941834920.72 ALAGOAS 2025 149677654365.77 156555737776.35 AMAPÁ 2020 293898632.97 303037488.89 AMAPÁ 2021 10307921519.26 10589605865.29 AMAPÁ 2022 22589496824.47 22993132159.04 AMAPÁ 2023 33348274807.29 34594476306.29 AMAPÁ 2024 49234167921.50 50899099314.68 AMAPÁ 2025 43800026149.18 44406299448.63 AMAZONAS 2020 1896416053.56 1904478519.22 AMAZONAS 2021 59602007146.92 60402524850.83 AMAZONAS 2022 137959984395.07 139605704304.32 AMAZONAS 2023 206589886936.57 207168568655.14 AMAZONAS 2024 320509222359.60 322753372109.09 AMAZONAS 2025 262501842566.55 262745433692.83 BAHIA 2020 5626168678.65 5723516293.28 BAHIA 2021 189627604775.12 188030937148.44 BAHIA 2022 414593212910.27 407065300763.51 BAHIA 2023 629370758844.41 612033024078.97 BAHIA 2024 951951631748.32 939705672093.63 BAHIA 2025 787591439629.34 794005593961.32 CEARÁ 2020 3471905937.26 3453467552.13 CEARÁ 2021 119792039246.49 118654961962.77 CEARÁ 2022 259798306115.07 257183061693.86 CEARÁ 2023 384146463366.49 389662338443.93 CEARÁ 2024 560039305007.08 576906499312.87 CEARÁ 2025 488323725303.29 502349883759.35 DISTRITO FEDERAL 2020 3779051742.51 3848147680.08 DISTRITO FEDERAL 2021 104020854876.64 106353689943.24 DISTRITO FEDERAL 2022 189656203082.58 184376261467.37 DISTRITO FEDERAL 2023 282369056438.91 268913652320.62 DISTRITO FEDERAL 2024 586241411458.06 437889088364.57 DISTRITO FEDERAL 2025 577162768961.48 398977465754.78 ESPÍRITO SANTO 2020 2491223037.49 2506335529.21 ESPÍRITO SANTO 2021 82240049104.97 80642735520.19 ESPÍRITO SANTO 2022 170969397657.82 171129842070.96 ESPÍRITO SANTO 2023 254704403441.22 256493179940.38 ESPÍRITO SANTO 2024 401117387538.10 406660799215.64 ESPÍRITO SANTO 2025 384950792618.95 390192423407.17 GOIÁS 2020 5362616300.09 5620026168.63 GOIÁS 2021 193709697189.22 196702947215.10 GOIÁS 2022 393390651454.47 395422959311.85 GOIÁS 2023 562892074419.80 557702833054.23 GOIÁS 2024 790948523459.39 791090590045.58 GOIÁS 2025 711053124575.26 713178243489.16 MARANHÃO 2020 1609913621.15 1643700382.27 MARANHÃO 2021 67322251562.95 71741732608.23 MARANHÃO 2022 158131221126.29 168887153306.80 MARANHÃO 2023 245616145853.47 261961768688.45 MARANHÃO 2024 410990335819.74 436948574056.18 MARANHÃO 2025 349605321219.62 367320886464.29 MATO GROSSO 2020 3109912885.77 3125410420.40 MATO GROSSO 2021 106620203649.89 105041768294.37 MATO GROSSO 2022 235489348235.13 235085733591.68 MATO GROSSO 2023 354039127804.25 354576411070.60 MATO GROSSO 2024 514447163296.72 524570867427.06 MATO GROSSO 2025 475589292915.31 488801641473.22 MATO GROSSO DO SUL 2020 1682315211.68 1693499745.10 MATO GROSSO DO SUL 2021 66218953623.57 66353752660.66 MATO GROSSO DO SUL 2022 137029721487.76 137371822772.82 MATO GROSSO DO SUL 2023 201295567947.29 205836997695.81 MATO GROSSO DO SUL 2024 284542959979.89 294084985576.98 MATO GROSSO DO SUL 2025 264176113409.40 270052177889.24 MINAS GERAIS 2020 12731091793.03 12735558646.56 MINAS GERAIS 2021 418597916869.08 431800975453.50 MINAS GERAIS 2022 852124125899.69 867200267479.34 MINAS GERAIS 2023 1239356589602.04 1256985048294.69 MINAS GERAIS 2024 1825382984279.42 1867543757796.54 MINAS GERAIS 2025 1656308143248.92 1689691342897.95 NAO INFORMADO 2020 68711760.34 64718567.45 NAO INFORMADO 2021 2032656311.92 3122788970.11 NAO INFORMADO 2022 4896255387.16 6632713627.87 NAO INFORMADO 2023 9014784353.15 8448368337.19 NAO INFORMADO 2024 17314411186.28 13837889923.51 NAO INFORMADO 2025 30859502248.93 23386029688.12 PARANÁ 2020 10527878521.52 10672267856.93 PARANÁ 2021 356623085100.18 352650532503.28 PARANÁ 

In [0]:
import pyspark.sql.functions as F

# Total recebido e pago por Região e Ano
df_regiao_ano = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.VL_RecebedorPF + df.VL_RecebedorPJ).alias("Total_Recebido"),
        F.sum(df.VL_PagadorPF + df.VL_PagadorPJ).alias("Total_Pago")
    )
    .orderBy("Regiao", "Ano")
)

display(df_regiao_ano)

Regiao Ano Total_Recebido Total_Pago CENTRO-OESTE 2020 13933896140.05 14287084014.21 CENTRO-OESTE 2021 470569709339.32 474452158113.37 CENTRO-OESTE 2022 955565924259.94 952256777143.72 CENTRO-OESTE 2023 1400595826610.25 1387029894141.26 CENTRO-OESTE 2024 2176180058194.06 2047635531414.19 CENTRO-OESTE 2025 2027981299861.45 1871009528606.40 NORDESTE 2020 19670043314.01 19759817512.47 NORDESTE 2021 685303701476.07 688229727941.67 NORDESTE 2022 1501421397063.34 1504254415128.01 NORDESTE 2023 2272451680344.73 2279235239961.43 NORDESTE 2024 3406644060290.35 3459513830559.73 NORDESTE 2025 2966402167195.50 3030976064954.14 NORTE 2020 7115723551.38 7255038468.89 NORTE 2021 254498170842.49 256631697002.29 NORTE 2022 569195439101.40 573697418905.91 NORTE 2023 835010957647.00 841996703186.53 NORTE 2024 1242220710005.81 1264059750859.45 NORTE 2025 1079212412272.95 1097162551864.87 Nao informado 2020 68711760.34 64718567.45 Nao informado 2021 2032656311.92 3122788970.11 Nao informado 2022 4896255387.16 6632713627.87 Nao informado 2023 9014784353.15 8448368337.19 Nao informado 2024 17314411186.28 13837889923.51 Nao informado 2025 30859502248.93 23386029688.12 SUDESTE 2020 67757030254.13 67209085646.17 SUDESTE 2021 2287179506988.90 2284658946740.44 SUDESTE 2022 4781076175758.35 4807509733538.38 SUDESTE 2023 7398969064819.00 7428315559799.91 SUDESTE 2024 11567890425054.20 11629489088377.25 SUDESTE 2025 10825016315327.69 10853595811459.95 SUL 2020 23741562950.18 23711223760.90 SUL 2021 822476592748.43 814972535083.48 SUL 2022 1662638132273.99 1630442265500.29 SUL 2023 2530658234806.34 2501674783154.15 SUL 2024 3710443284659.49 3706156858256.06 SUL 2025 3297761280186.90 3351102990519.94

In [0]:
import pyspark.sql.functions as F


df_pf_ano = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.QT_PES_PagadorPF).alias("Quantidade de Pessoas Físicas Pagadoras"),
    )
    .orderBy("Regiao", "Ano")
)

display(df_pf_ano)

Regiao Ano Quantidade de Pessoas Físicas Pagadoras CENTRO-OESTE 2020 3317265 CENTRO-OESTE 2021 64435287 CENTRO-OESTE 2022 94709511 CENTRO-OESTE 2023 112865129 CENTRO-OESTE 2024 126461855 CENTRO-OESTE 2025 100521107 NORDESTE 2020 6489066 NORDESTE 2021 151715445 NORDESTE 2022 257022434 NORDESTE 2023 329603625 NORDESTE 2024 382520222 NORDESTE 2025 307495733 NORTE 2020 2420574 NORTE 2021 52981824 NORTE 2022 87198773 NORTE 2023 109977603 NORTE 2024 127180679 NORTE 2025 102877552 Nao informado 2020 21543 Nao informado 2021 500945 Nao informado 2022 870839 Nao informado 2023 1223526 Nao informado 2024 1559160 Nao informado 2025 1282734 SUDESTE 2020 17886632 SUDESTE 2021 349048889 SUDESTE 2022 512192911 SUDESTE 2023 608096412 SUDESTE 2024 679020513 SUDESTE 2025 539028464 SUL 2020 4813463 SUL 2021 104576819 SUL 2022 160540765 SUL 2023 193586152 SUL 2024 219973820 SUL 2025 176319821

In [0]:
import pyspark.sql.functions as F


df_pj_ano = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.QT_PES_PagadorPJ ).alias("Quantidade de Pessoas Jurídicas Pagadoras"),
    )
    .orderBy("Regiao", "Ano")
)

display(df_pj_ano)

In [0]:
import pyspark.sql.functions as F


df_recebedor_pj_ano = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.QT_PES_RecebedorPJ ).alias("Quantidade de Pessoas Jurídicas Recebedoras"),
    )
    .orderBy("Regiao", "Ano")
)

display(df_recebedor_pj_ano)

In [0]:
import pyspark.sql.functions as F


df_recebedor_pf_ano = (
    df.groupBy(
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        F.sum(df.QT_PES_RecebedorPF ).alias("Quantidade de Pessoas Físicas Recebedoras"),
    )
    .orderBy("Regiao", "Ano")
)

display(df_recebedor_pf_ano)

In [0]:
import pyspark.sql.functions as F

df_consolidado_municipio = (
    df.groupBy(
        df.Municipio_Ibge,
        df.Municipio,
        df.Estado,
        df.Regiao,
        F.year(df.AnoMes).alias("Ano")
    ).agg(
        # Valores pagos
        F.sum(df.VL_PagadorPF).alias("Total_Pago_PF"),
        F.sum(df.VL_PagadorPJ).alias("Total_Pago_PJ"),
        F.sum(df.VL_PagadorPF + df.VL_PagadorPJ).alias("Total_Pago"),
        
        # Valores recebidos
        F.sum(df.VL_RecebedorPF).alias("Total_Recebido_PF"),
        F.sum(df.VL_RecebedorPJ).alias("Total_Recebido_PJ"),
        F.sum(df.VL_RecebedorPF + df.VL_RecebedorPJ).alias("Total_Recebido"),
        
        # Quantidades
        F.sum(df.QT_PES_PagadorPF).alias("Qtd_Pagadores_PF"),
        F.sum(df.QT_PES_PagadorPJ).alias("Qtd_Pagadores_PJ"),
        F.sum(df.QT_PES_RecebedorPF).alias("Qtd_Recebedores_PF"),
        F.sum(df.QT_PES_RecebedorPJ).alias("Qtd_Recebedores_PJ"),
        
        # Saldo
        (F.sum(df.VL_RecebedorPF + df.VL_RecebedorPJ) - 
         F.sum(df.VL_PagadorPF + df.VL_PagadorPJ)).alias("Saldo")
    )
    .orderBy("Estado", "Municipio", "Ano")
)

display(df_consolidado_municipio)

df_consolidado_municipio.write.mode("overwrite").saveAsTable('pix_consolidado')



Municipio_Ibge Municipio Estado Regiao Ano Total_Pago_PF Total_Pago_PJ Total_Pago Total_Recebido_PF Total_Recebido_PJ Total_Recebido Qtd_Pagadores_PF Qtd_Pagadores_PJ Qtd_Recebedores_PF Qtd_Recebedores_PJ Saldo 1200013 ACRELÂNDIA ACRE NORTE 2020 1571376.76 1241994.92 2813371.68 1462569.17 1282036.39 2744605.56 991 42 870 49 -68766.12 1200013 ACRELÂNDIA ACRE NORTE 2021 95893657.98 61112340.60 157005998.58 95026620.01 55199944.54 150226564.55 29772 1699 28111 1723 -6779434.03 1200013 ACRELÂNDIA ACRE NORTE 2022 241856536.67 109555847.21 351412383.88 243966227.50 95535803.43 339502030.93 56464 2720 54797 2762 -11910352.95 1200013 ACRELÂNDIA ACRE NORTE 2023 383711662.86 142994009.76 526705672.62 391338961.90 114206142.03 505545103.93 75856 3302 73360 3364 -21160568.69 1200013 ACRELÂNDIA ACRE NORTE 2024 614636123.37 198359147.93 812995271.30 627622097.57 161921551.06 789543648.63 89923 3794 87111 3741 -23451622.67 1200013 ACRELÂNDIA ACRE NORTE 2025 575508365.47 158603233.92 734111599.39 611890684.20 139684639.00 751575323.20 73763 3006 71307 3015 17463723.81 1200054 ASSIS BRASIL ACRE NORTE 2020 356376.44 11240.65 367617.09 398063.94 11153.62 409217.56 292 7 319 7 41600.47 1200054 ASSIS BRASIL ACRE NORTE 2021 24232424.44 4236843.83 28469268.27 23287853.06 2806429.17 26094282.23 9582 243 9897 227 -2374986.04 1200054 ASSIS BRASIL ACRE NORTE 2022 66880050.36 15271573.07 82151623.43 67470887.50 7312254.58 74783142.08 19752 690 20510 639 -7368481.35 1200054 ASSIS BRASIL ACRE NORTE 2023 115404978.77 20020372.52 135425351.29 112154453.15 14030875.75 126185328.90 30925 986 30721 832 -9240022.39 1200054 ASSIS BRASIL ACRE NORTE 2024 195238347.52 39209692.18 234448039.70 190285995.23 25118699.64 215404694.87 39978 1242 39557 974 -19043344.83 1200054 ASSIS BRASIL ACRE NORTE 2025 191939384.08 48451925.15 240391309.23 184168223.97 33690027.36 217858251.33 35521 1044 34767 948 -22533057.90 1200104 BRASILÉIA ACRE NORTE 2020 3883371.39 19076474.38 22959845.77 4091088.30 14333638.50 18424726.80 1820 83 1874 94 -4535118.97 1200104 BRASILÉIA ACRE NORTE 2021 211925174.40 235791454.82 447716629.22 218825852.41 177306277.48 396132129.89 55638 2859 57557 2827 -51584499.33 1200104 BRASILÉIA ACRE NORTE 2022 435769061.44 350629083.71 786398145.15 437216310.19 302051048.56 739267358.75 104964 5058 108335 4987 -47130786.40 1200104 BRASILÉIA ACRE NORTE 2023 682683812.00 612451304.54 1295135116.54 702764433.01 537701264.84 1240465697.85 146683 6358 147127 6164 -54669418.69 1200104 BRASILÉIA ACRE NORTE 2024 1123877262.99 1304534382.15 2428411645.14 1108448769.71 1175154703.55 2283603473.26 184644 7439 181738 7001 -144808171.88 1200104 BRASILÉIA ACRE NORTE 2025 1105006617.25 846581368.95 1951587986.20 1092160309.83 739556382.95 1831716692.78 154716 6260 152422 5978 -119871293.42 1200138 BUJARI ACRE NORTE 2020 795662.74 673131.76 1468794.50 906184.84 646213.99 1552398.83 581 22 571 18 83604.33 1200138 BUJARI ACRE NORTE 2021 44627758.57 35599007.37 80226765.94 45885870.00 29016728.64 74902598.64 17874 653 19484 573 -5324167.30 1200138 BUJARI ACRE NORTE 2022 111799810.55 53637955.90 165437766.45 112350523.48 39825178.51 152175701.99 35601 1160 37545 1040 -13262064.46 1200138 BUJARI ACRE NORTE 2023 176307499.37 63292667.76 239600167.13 177904956.88 57018832.12 234923789.00 50476 1277 51274 1183 -4676378.13 1200138 BUJARI ACRE NORTE 2024 306121725.38 105750566.27 411872291.65 305587474.13 91276157.31 396863631.44 64136 1645 63658 1478 -15008660.21 1200138 BUJARI ACRE NORTE 2025 273060362.72 106631948.07 379692310.79 279255155.28 92567469.17 371822624.45 54469 1263 53895 1200 -7869686.34 1200179 CAPIXABA ACRE NORTE 2020 525661.79 161291.54 686953.33 609258.37 236969.35 846227.72 475 18 510 16 159274.39 1200179 CAPIXABA ACRE NORTE 2021 41656260.35 8260400.22 49916660.57 39322805.19 9076991.65 48399796.84 15605 473 16548 452 -1516863.73 1200179 CAPIXABA ACRE NORTE 2022 103506112.94 16428550.53 119934663.47 101263824.69 18147603.07 119411427.76 31037 833 31870 759 -523235.71

---------------------------------------------------------------------------
PySparkTypeError                          Traceback (most recent call last)
File <command-8813724497006516>, line 38
     34 display(df_consolidado_municipio)
     36 df_consolidado_municipio.write.mode("overwrite").saveAsTable('pix_consolidado')
---> 38 spark.sql("DESCRIBE DETAIL pix_consolidado").show(False)

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/dataframe.py:1123, in DataFrame.show(self, n, truncate, vertical)
   1122 def show(self, n: int = 20, truncate: Union[bool, int] = True, vertical: bool = False) -> None:
-> 1123     print(self._show_string(n, truncate, vertical))

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/dataframe.py:843, in DataFrame._show_string(self, n, truncate, vertical)
    839 def _show_string(
    840     self, n: int = 20, truncate: Union[bool, int] = True, vertical: bool = False
    841 ) -> str:
    842     if not isinstanc

In [0]:
spark.sql("DESCRIBE DETAIL pix_consolidado").show(100)

+------+--------------------+--------------------+-----------+--------+--------------------+-------------------+----------------+-----------------+--------+-----------+--------------------+----------------+----------------+--------------------+--------------------+-------------+
|format|                  id|                name|description|location|           createdAt|       lastModified|partitionColumns|clusteringColumns|numFiles|sizeInBytes|          properties|minReaderVersion|minWriterVersion|       tableFeatures|          statistics|clusterByAuto|
+------+--------------------+--------------------+-----------+--------+--------------------+-------------------+----------------+-----------------+--------+-----------+--------------------+----------------+----------------+--------------------+--------------------+-------------+
| delta|fed1bd67-0188-42b...|workspace.default...|       NULL|        |2025-11-02 12:15:...|2025-11-02 12:24:29|              []|               []|       1|    